In [1]:
import holoviews as hv
import geoviews as gv
from holoviews import opts, streams
from cartopy import crs
import numpy as np
import pyproj
import libgsidem2el as gsi

hv.extension('bokeh', logo=False)
gv.extension('bokeh', logo=False)

# make Line object

 - Polydraw
  * actions: http://holoviews.org/reference/streams/bokeh/PolyDraw.html#bokeh-gallery-polydraw

In [4]:
outcrs = crs.epsg(6677)
url = 'https://cyberjapandata.gsi.go.jp/xyz/seamlessphoto/{Z}/{X}/{Y}.jpg'
geomap = gv.WMTS(url, crs=outcrs)

path = gv.Path([[(0,0),(100,100)]], crs=outcrs)
path_stream = streams.PolyDraw(source=path, drag=False, show_vertices=True)

geo = geomap * path.opts( opts.Path(color='red', line_width=5) )
f = geo.options(width=600, height=400)
f

:Overlay
   .WMTS.I :WMTS   [Longitude,Latitude]
   .Path.I :Path   [Longitude,Latitude]

In [5]:
path_stream 

PolyDraw(data={'xs': [array([-2.2939349e-09,  1.0000000e+02])], 'ys': [array([2.99391868e-25, 1.00000000e+02])]})

# output location.html

In [2]:
data={'xs': [np.array([-3367.73567716, -3290.62303946])], 'ys': [np.array([-26307.68964812, -26975.23822235])]}

In [6]:
outcrs = crs.epsg(6677)
url = 'https://cyberjapandata.gsi.go.jp/xyz/seamlessphoto/{Z}/{X}/{Y}.jpg'
geomap = gv.WMTS(url, crs=outcrs)
xs = data['xs'][0]
ys = data['ys'][0]
p0, p1 = np.array([xs[0], ys[0]]), np.array( [xs[1], ys[1]] )

path = gv.Path([[p0,p1]], crs=outcrs)
geo = geomap * path.opts( opts.Path(color='red', line_width=5) )
f = geo.options(width=400, height=300)
hv.save(f, 'location.html')
f

:Overlay
   .WMTS.I :WMTS   [Longitude,Latitude]
   .Path.I :Path   [Longitude,Latitude]

# make geojson

 - 3D multipoint 
 - get Elevation tools : https://github.com/computational-sediment-hyd/libgsidem2el

In [7]:
# data = path_stream.data

xs = data['xs'][0]
ys = data['ys'][0]
p0, p1 = np.array([xs[0], ys[0]]), np.array( [xs[1], ys[1]] )

# unit vector
d = p1 - p0
L = np.sqrt(d[0]**2 + d[1]**2)
e = d / L

dx = 5
point = np.array( [p0 + x * e for x in np.arange(0, L, dx)] )

dem = gsi.libgsidem2el('DEM5A')

EPSGout = pyproj.Proj("+init=EPSG:6668")
EPSGin = pyproj.Proj("+init=EPSG:6677")

z = []
for p in point:
    lon, lat = pyproj.transform( EPSGin, EPSGout, *p)
    zt = dem.getEL(lon, lat, zoom = 15)
    if type(zt) is str : zt = np.nan 
    z.append( zt )

z = np.array(z, dtype=np.float)
point3d = np.hstack([point, np.array([z]).T])

In [18]:
point3d

array([[-3.36773568e+03, -2.63076896e+04, -1.20000000e-01],
       [-3.36716191e+03, -2.63126566e+04, -9.00000000e-02],
       [-3.36658815e+03, -2.63176236e+04, -8.00000000e-02],
       [-3.36601438e+03, -2.63225906e+04, -1.00000000e-01],
       [-3.36544062e+03, -2.63275575e+04, -1.30000000e-01],
       [-3.36486685e+03, -2.63325245e+04, -1.50000000e-01],
       [-3.36429309e+03, -2.63374915e+04, -1.20000000e-01],
       [-3.36371932e+03, -2.63424584e+04,  0.00000000e+00],
       [-3.36314556e+03, -2.63474254e+04, -2.00000000e-02],
       [-3.36257179e+03, -2.63523924e+04, -8.00000000e-02],
       [-3.36199802e+03, -2.63573594e+04, -3.40000000e-01],
       [-3.36142426e+03, -2.63623263e+04, -6.00000000e-02],
       [-3.36085049e+03, -2.63672933e+04,  6.00000000e-02],
       [-3.36027673e+03, -2.63722603e+04,  8.00000000e-02],
       [-3.35970296e+03, -2.63772272e+04, -6.00000000e-02],
       [-3.35912920e+03, -2.63821942e+04, -1.40000000e-01],
       [-3.35855543e+03, -2.63871612e+04

In [17]:
LineString(point3d).wkt

'LINESTRING Z (-3367.73567716 -26307.68964812 -0.12, -3367.161911906202 -26312.65661836689 -0.09, -3366.588146652404 -26317.62358861379 -0.08, -3366.014381398606 -26322.59055886068 -0.1, -3365.440616144809 -26327.55752910758 -0.13, -3364.866850891011 -26332.52449935447 -0.15, -3364.293085637213 -26337.49146960137 -0.12, -3363.719320383415 -26342.45843984826 0, -3363.145555129617 -26347.42541009515 -0.02, -3362.571789875819 -26352.39238034205 -0.08, -3361.998024622022 -26357.35935058894 -0.34, -3361.424259368224 -26362.32632083584 -0.06, -3360.850494114426 -26367.29329108273 0.06, -3360.276728860628 -26372.26026132963 0.08, -3359.702963606831 -26377.22723157652 -0.06, -3359.129198353033 -26382.19420182341 -0.14, -3358.555433099235 -26387.16117207031 -0.19, -3357.981667845437 -26392.1281423172 -0.19, -3357.407902591639 -26397.0951125641 -0.19, -3356.834137337841 -26402.06208281099 -0.2, -3356.260372084043 -26407.02905305789 0.03, -3355.686606830246 -26411.99602330478 1.3, -3355.112841576

In [8]:
import json
from shapely.geometry import mapping, LineString

j = {
"type": "FeatureCollection",
"name": "area",
"crs": { "type": "name", "properties": { "name": "urn:ogc:def:crs:EPSG::6677" } },
"features": [
{ "type": "Feature", "properties": { "id": 1 }, "geometry":mapping( LineString(point3d) ) }
]
}

In [9]:
import pprint
pprint.pprint(j)

{'crs': {'properties': {'name': 'urn:ogc:def:crs:EPSG::6677'}, 'type': 'name'},
 'features': [{'geometry': {'coordinates': ((-3367.73567716,
                                             -26307.68964812,
                                             -0.12),
                                            (-3367.161911906202,
                                             -26312.65661836689,
                                             -0.09),
                                            (-3366.5881466524042,
                                             -26317.623588613787,
                                             -0.08),
                                            (-3366.0143813986065,
                                             -26322.59055886068,
                                             -0.1),
                                            (-3365.4406161448087,
                                             -26327.557529107577,
                                             -0.13),
        

In [10]:
with open("sections.geojson", "w") as f:
    json.dump(j, f)

# load geojson, plot-graph

In [11]:
import geopandas as gpd
gdf = gpd.read_file("sections.geojson")
gdf

id                                           geometry
0   1  LINESTRING Z (-3367.73567716 -26307.68964812 -...

In [12]:
point = np.array( gdf.geometry[0].coords[:] )
# drop z
pointxy = point[:,:2]
L = np.linalg.norm( pointxy - pointxy[0],ord=2,axis=1 )
z = point[:,-1]

In [13]:
f = hv.Curve((L,z)).options(width=400, height=300)
hv.save(f, 'figsection.html')
f

:Curve   [x]   (y)